In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.layers import Dense, Input, LeakyReLU, BatchNormalization
from tensorflow.keras.models import Model
from sklearn.preprocessing import MinMaxScaler, LabelEncoder
from sklearn.model_selection import train_test_split
import time

# Đọc DataFrame 'transaction'
transaction_df = pd.read_csv('../balanced_transaction-from-to-prefix-22-KLTN-newtime.csv')

# ############## Loại bỏ các transaction trùng lặp ##############
# df = transaction_df.drop_duplicates(subset=['from_address', 'from_address'], inplace=False)
# # Lấy tất cả địa chỉ bất thường (nhãn 1)
# abnormal_addresses = df[df['label'] == 1]

# # Tính số lượng địa chỉ bình thường cần lấy
# num_normal_addresses = int(len(abnormal_addresses) / 0.46 * 0.54)

# # Lấy ngẫu nhiên các địa chỉ bình thường
# normal_addresses = df[df['label'] == 0].sample(num_normal_addresses, random_state=42)

# # Kết hợp các địa chỉ bất thường và bình thường
# balanced_df = pd.concat([abnormal_addresses, normal_addresses])

# # Trộn lại tập dữ liệu
# transaction_df = balanced_df.sample(frac=1, random_state=42).reset_index(drop=True)
# print(transaction_df.shape)

# #################################################################

# # Tạo DataFrame 'data' để lưu kết quả
# data_df = pd.DataFrame(columns=['hash', 'image', 'label'])

# # Đọc cột 'hash' và 'label'
# hash_values = transaction_df['hash']
# label_values = transaction_df['label']

# # Khởi tạo biến đếm
# loop_counter = 1

# # Duyệt qua từng giá trị hash và label
# for hash_value, label_value in zip(hash_values, label_values):
#     # Tạo tên file từ giá trị hash
#     filename = f'./dataset/x7/data/_{hash_value}_data.txt'

#     try:
#         # Đọc nội dung từ file
#         data = np.genfromtxt(filename, delimiter='\t')
#         # image = pd.read_csv(filename)

#         # Kiểm tra kích thước mảng
#         if data.shape == (7, 7):
#             # Tạo một hàng mới trong DataFrame 'data'
#             new_row = pd.DataFrame({'hash': [hash_value], 'image': [data], 'label': [label_value]})
#             data_df = pd.concat([data_df, new_row], ignore_index=True)
#         else:
#             print(f"Kích thước mảng không phù hợp trong file {filename}")
#     except FileNotFoundError:
#         print(f"Không tìm thấy file {filename}")

#     # In ra lần chạy thứ n của vòng lặp
#     print(f"Lần chạy thứ {loop_counter}")
#     loop_counter += 1

#     # if loop_counter == 4:
#     #   break

# # In ra DataFrame 'data'
# print(data_df.shape)
# print(data_df.head(3))

In [2]:
######### Convert manual #########
# Chuyển đổi DataFrame thành mảng NumPy

replace_nan = transaction_df.replace(np.nan, -1)

X = replace_nan.drop(columns=['hash','from_address','to_address','label'], axis=1).values

# Padding giá trị -2 để có số lượng đặc trưng là bội số của 49
num_padding = 49 - X.shape[1] % 49
X_padded = np.pad(X, ((0, 0), (0, num_padding)), mode='constant', constant_values=-2)

# Tiền xử lý dữ liệu
scaler = MinMaxScaler()
normalized_data = scaler.fit_transform(X_padded)

# Reshape mảng thành ma trận 3 chiều 4x4
X_reshaped = normalized_data.reshape(-1, 7, 7)

print(X_reshaped[0])

######### Convert image #########
# image_arrays = data_df['image'].tolist()
# # Tạo numpy array từ danh sách các mảng 2D
# np_images = np.stack(image_arrays, axis=0)

# Chia dữ liệu thành tập huấn luyện và tập kiểm tra
X_train, X_test, y_train, y_test = train_test_split(X_reshaped, transaction_df['label'].values, test_size=0.2, random_state=42)
# print(type(X_train))
# print(type(y_train))

[[9.81037152e-02 2.89604821e-01 9.90888919e-02 1.64745564e-01
  1.98023835e-02 3.52191235e-01 1.03305785e-01]
 [5.09593767e-06 1.23760689e-03 5.17312733e-04 7.93691456e-23
  6.21459592e-04 9.58204334e-02 4.86963579e-03]
 [8.27284011e-04 1.96981912e-02 0.00000000e+00 4.91450481e-04
  4.80016893e-04 2.89604736e-01 3.77547433e-07]
 [0.00000000e+00 1.11242759e-01 2.89604824e-01 1.02923700e-01
  3.70677520e-01 4.82081161e-03 3.87484641e-02]
 [2.49713870e-03 5.04349160e-06 2.53652007e-05 2.92663004e-05
  0.00000000e+00 7.31399700e-04 2.50379056e-01]
 [6.41445215e-03 2.38282480e-03 4.80286476e-02 3.03030303e-21
  9.88033052e-04 3.65578858e-04 2.89604736e-01]
 [3.16621317e-07 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00]]


In [3]:
# Required Libraries
from keras.models import Model
from keras.layers import Input, Dense, Conv2D, LeakyReLU, Dropout, Flatten, Lambda, Activation, Reshape, Conv2DTranspose, Conv1DTranspose, Conv1D
# from keras.utils.vis_utils import plot_model
from keras.datasets.mnist import load_data
from keras import backend as K
from tensorflow.keras.optimizers import Adam
from numpy.random import randn, randint
from numpy import expand_dims, zeros, ones, asarray
from matplotlib import pyplot



# load the images
def load_real_samples(n_classes=10):
    # (trainX, trainy), (_, _) = load_data()
    trainX, _, trainy, _ = train_test_split(X_reshaped, transaction_df['label'].values, test_size=0.2, random_state=42)

    # print(trainX.shape, trainy.shape)
    # print(type(trainX))
    # print(trainX[0])
    # print(type(trainX[0][0]))
    # print(type(trainy))
    # print(trainy[2])
    X = expand_dims(trainX, axis=-1)
    X = X.astype('float32')
    trainy = trainy.astype('uint8')
    # scale from [0,255] to [0,1] as we will be using tanh activation.
#     X = X / 255.0

    # Convert pandas to numpy for trainy
    # trainy = trainy.values
    # print(X[0])
    # print(type(X))
    # print(X.shape, trainy.shape)
    return [X, trainy]

data = load_real_samples()



In [ ]:
from numpy import expand_dims, zeros, ones, asarray
from numpy.random import randn, randint

from keras.datasets.mnist import load_data
from keras.optimizers import Adam
from keras.models import Model, Sequential

from keras.layers import Input, Dense, Reshape, Flatten, Conv2D, Conv2DTranspose, MaxPooling2D
from keras.layers import LeakyReLU, Dropout, Lambda, Activation
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score, confusion_matrix

#from keras.utils import to_categorical

from matplotlib import pyplot as plt
from keras import backend as K
import numpy as np

np.random.seed(42)

# define the standalone generator model
def define_generator(latent_dim):

	in_lat = Input(shape=(latent_dim,))
	#Start with enough dense nodes to be reshaped and ConvTransposed to 28x28x1
	n_nodes = 256 * 7 * 7
	X = Dense(n_nodes)(in_lat)
	X = LeakyReLU(alpha=0.2)(X)
	X = Reshape((7, 7, 256))(X)

	X = Conv2DTranspose(128, (2,2), strides=(1,1), padding='same')(X) #14x14x128
	X = LeakyReLU(alpha=0.2)(X)

	X = Conv2DTranspose(64, (2,2), strides=(1,1), padding='same')(X) #14x14x64
	X = LeakyReLU(alpha=0.2)(X)
	# output
	out_layer = Conv2DTranspose(1, (2,2), strides=(1,1), activation='sigmoid',
                             padding='same')(X) #28x28x1
	# define model
	model = Model(in_lat, out_layer)
	return model

# gen_model=define_generator(100)
# print(gen_model.summary())

# define the base discriminator model for sup and unsup discriminators
#This is the base discriminator that supervised and unsupervised are going to share weights from.
#(I know that the above ssentence is bad english!!!)
def define_discriminator(in_shape=(7,7,1), n_classes=2):
    in_image = Input(shape=in_shape)
    X = Conv2D(32, (2,2), strides=(2,2), padding='same')(in_image)
    X = LeakyReLU(alpha=0.2)(X)

    X = Conv2D(64, (2,2), strides=(2,2), padding='same')(X)
    X = LeakyReLU(alpha=0.2)(X)

    X = Conv2D(128, (2,2), strides=(2,2), padding='same')(X)
    X = LeakyReLU(alpha=0.2)(X)

    X = Flatten()(X)
    X = Dropout(0.4)(X) #Consider adding more dropout layers to minimize overfitting - remember we work with limited labeled data.
    X = Dense(n_classes)(X)

    model = Model(inputs=in_image, outputs=X)

    return model

#Define the supervised discriminator.
#Multiclass classification, so we will use softmax activation.
#To avoid converting our labels to categorical, we will work with sparse categorical crossentropy loss.
def define_sup_discriminator(disc):
    model=Sequential()
    model.add(disc)
    model.add(Activation('sigmoid'))
    #Let us use sparse categorical loss so we dont have to convert our Y to categorical
    model.compile(optimizer=Adam(learning_rate=0.0001, beta_1=0.5),
                  loss="sparse_categorical_crossentropy",metrics=['accuracy'])
    return model


#Define the unsupervised discriminator
#Takes the output of the supervised, just before the softmax activation.
#Then, adds a layer with calculation of sum of exponential outputs. (defined below as custom_activation)
# Reference: https://arxiv.org/abs/1606.03498

#This custom activation layer gives a value close to 0 for smaller activations
#in the prior discriminator layer. It gives values close to 1 for large activations.
#This way it gives low activation for fake images. No need for sigmoid anymore.

# custom activation function for the unsupervised discriminator
#D(x) = Z(x) / (Z(x) + 1) where Z(x) = sum(exp(l(x))). l(x) is the output from sup discr. prior to softmax
def custom_activation(x):
    Z_x = K.sum(K.exp(x), axis=-1, keepdims=True)
    D_x = Z_x /(Z_x+1)

    return D_x

#You can also try the built in tensorflow function: tf.reduce_logsumexp(class_logits, 1)

def define_unsup_discriminator(disc):
    model=Sequential()
    model.add(disc)
    model.add(Lambda(custom_activation))
    model.compile(loss='binary_crossentropy', optimizer=Adam(learning_rate=0.0001, beta_1=0.5))
    return model


# disc=define_discriminator()
# disc_sup=define_sup_discriminator(disc)
# disc_unsup=define_unsup_discriminator(disc)
# print(disc_unsup.summary())


# define the combined generator and discriminator model, for updating the generator
def define_gan(gen_model, disc_unsup):

	disc_unsup.trainable = False # make unsup. discriminator not trainable
	gan_output = disc_unsup(gen_model.output) #Gen. output is the input to disc.
	model = Model(gen_model.input, gan_output)
	model.compile(loss='binary_crossentropy', optimizer=Adam(learning_rate=0.0001, beta_1=0.5))
	return model

# gan_model = define_gan(gen_model, disc_unsup)
# print(gan_model.summary())

#select subset of the dataset for supervised training
#Let us pick only 100 samples to be used in supervised training.
#Also, we need to ensure we pick 10 samples per class to ensure a good balance
#of data between classes.
def select_supervised_samples(dataset, n_samples=5000, n_classes=2):
 	print('test select')
 	X, y = dataset
 	X_list, y_list = list(), list()
 	n_per_class = int(n_samples / n_classes) #Number of amples per class.
 	for i in range(n_classes):
         X_with_class = X[y == i] # get all images for this class
         ix = np.random.randint(0, len(X_with_class), n_per_class) # choose random images for each class
         print(ix)
         [X_list.append(X_with_class[j]) for j in ix] # add to list
         [y_list.append(i) for j in ix]
 	return asarray(X_list), asarray(y_list) #Returns a list of 2 numpy arrays corresponding to X and Y


# Pick real samples from the dataset.
#Return both images and corresponding labels in addition to y=1 indicating that the images are real.
#Remember that we will not use the labels for unsupervised, only used for supervised.
def generate_real_samples(dataset, n_samples):

	images, labels = dataset
	ix = randint(0, images.shape[0], n_samples)
	X, labels = images[ix], labels[ix] #Select random images and corresponding labels
	y = ones((n_samples, 1)) #Label all images as 1 as these are real images. (for the discriminator training)
	return [X, labels], y

# generate latent points, to be used as inputs to the generator.
def generate_latent_points(latent_dim, n_samples):
	z_input = randn(latent_dim * n_samples)
	z_input = z_input.reshape(n_samples, latent_dim) # reshape for input to the network
	return z_input

# Generate fake images using the generator and above latent points as input to it.
#We do not care about labeles so the generator will not know anything about the labels.
def generate_fake_samples(generator, latent_dim, n_samples):

	z_input = generate_latent_points(latent_dim, n_samples)
	fake_images = generator.predict(z_input)
	# create class labels
	y = zeros((n_samples, 1)) #Label all images as 0 as these are fake images. (for the discriminator training)
	return fake_images, y

# report accuracy and save plots & the model periodically.
def summarize_performance(step, bat_per_epo, gen_model, disc_sup, latent_dim, dataset, n_samples=100):
	global max_accuracy
	# Generate fake images
	X, _ = generate_fake_samples(gen_model, latent_dim, n_samples)

# 	X = (X + 1) / 2.0 # scale to [0,1] for plotting
# 	# plot images
# 	for i in range(100):
# 		plt.subplot(10, 10, 1 + i)
# 		plt.axis('off')
# 		plt.imshow(X[i, :, :, 0], cmap='gray_r')
# 	# save plot to drive
# 	filename1 = 'generated_plot_%04d.png' % (step+1)
# 	plt.savefig(filename1)
# 	plt.close()

	# evaluate the discriminator
	X, y = dataset
	_, acc = disc_sup.evaluate(X, y, verbose=0)
    
    # Lấy thời gian bắt đầu
	start_time = time.perf_counter()
    
	y_pred=disc_sup.predict(X_test)
    
	# Lấy thời gian kết thúc
	end_time = time.perf_counter()
	# Tính thời gian thực thi (đơn vị: giây)
	execution_time = end_time - start_time
	# Chuyển đơi sang đơn vị micro giây
	execution_time_microseconds = execution_time * 1000000
	print(f"Thời gian thực thi: {execution_time_microseconds:.2f} micro giây")

	y_pred=np.argmax(y_pred,axis=1)
	accuracy = accuracy_score(y_test, y_pred)
	if accuracy > max_accuracy:
		max_accuracy = acc
        
		f1 = f1_score(y_test, y_pred)
		tn, fp, fn, tp = confusion_matrix(y_test, y_pred).ravel()
		# Tính toán dương tính giả (false positive rate)
		fpr = fp / (fp + tn)

		print(f"Dương tính giả (false positive rate): {fpr:.4f}")
		with open('max_accuracy-22.txt', 'w') as file:
			# Ghi nội dung vào file
			file.write('Epoch ' + str(((step+1) / bat_per_epo)) + ' - Accuracy: ' + str(max_accuracy) 
            + '- F1_score: ' + str(f1) + '- FPR: ' + str(fpr))
	print('Discriminator Accuracy: %.3f%%' % (acc * 100))
	# save the generator model
# 	filename2 = './Result-ML/SGAN-255/Test_20/gen_model_%04d.h5' % (step+1)
# 	gen_model.save(filename2)
	# save the Discriminator (classifier) model
	filename3 = './Result-ML/final/disc_sup_%04d.h5' % ((step+1) / bat_per_epo)
	disc_sup.save(filename3)
# 	print('>Saved: %s, %s, and %s' % (filename1, filename2, filename3))

# train the generator and discriminator
def train(gen_model, disc_unsup, disc_sup, gan_model, dataset, latent_dim, n_epochs=20, n_batch=32):

    # select supervised dataset for training.
    #Remember that we are not using all 60k images, just a subset (100 images, 10 per class. )
	X_sup, y_sup = select_supervised_samples(dataset)
	#print(X_sup.shape, y_sup.shape)

	bat_per_epo = int(dataset[0].shape[0] / n_batch)
	# iterations
	n_steps = bat_per_epo * n_epochs

	half_batch = int(n_batch / 2)
	print('n_epochs=%d, n_batch=%d, 1/2=%d, b/e=%d, steps=%d' % (n_epochs,
                                                              n_batch, half_batch,
                                                              bat_per_epo, n_steps))

    #  enumerate epochs
	for i in range(n_steps):
		# update supervised discriminator (disc_sup) on real samples.
        #Remember that we use real labels to train as this is supervised.
        #This is the discriminator we really care about at the end.
        #Also, this is a multiclass classifier, not binary. Therefore, our y values
        #will be the real class labels for MNIST. (NOT 1 or 0 indicating real or fake.)
		[Xsup_real, ysup_real], _ = generate_real_samples([X_sup, y_sup], half_batch)
		sup_loss, sup_acc = disc_sup.train_on_batch(Xsup_real, ysup_real)

		# update unsupervised discriminator (disc_unsup) - just like in our regular GAN.
        #Remember that we will not train on labels as this is unsupervised, just binary as in our regular GAN.
        #The y_real below indicates 1s telling the discriminator that these images are real.
        #do not confuse this with class labels.
        #We will discard this discriminator at the end.
		[X_real, _], y_real = generate_real_samples(dataset, half_batch) #
		d_loss_real = disc_unsup.train_on_batch(X_real, y_real)
        #Now train on fake.
		X_fake, y_fake = generate_fake_samples(gen_model, latent_dim, half_batch)
		d_loss_fake = disc_unsup.train_on_batch(X_fake, y_fake)

		# update generator (gen) - like we do in regular GAN.
        #We can discard this model at the end as our primary goal is to train a multiclass classifier (sup. disc.)
		X_gan, y_gan = generate_latent_points(latent_dim, n_batch), ones((n_batch, 1))
		gan_loss = gan_model.train_on_batch(X_gan, y_gan)

		# summarize loss on this batch
		print('>%d, c[%.3f,%.0f], d[%.3f,%.3f], g[%.3f]' % (i+1, sup_loss, sup_acc*100, d_loss_real, d_loss_fake, gan_loss))
		# evaluate the model performance periodically
		if (i+1) % (bat_per_epo * 1) == 0:
			summarize_performance(i, bat_per_epo, gen_model, disc_sup, latent_dim, dataset)

#################################################################################
# TRAIN
#################################

latent_dim = 100

# create the discriminator models
disc=define_discriminator() #Bare discriminator model...
disc_sup=define_sup_discriminator(disc) #Supervised discriminator model
disc_unsup=define_unsup_discriminator(disc) #Unsupervised discriminator model.

gen_model = define_generator(latent_dim) #Generator
gan_model = define_gan(gen_model, disc_unsup) #GAN
dataset = load_real_samples() #Define the dataset by loading real samples. (This will be a list of 2 numpy arrays, X and y)

max_accuracy = 0

# train the model
# NOTE: 1 epoch = 600 steps in this example.
train(gen_model, disc_unsup, disc_sup, gan_model, dataset, latent_dim, n_epochs=8000, n_batch=32)



test select
[15795   860  5390 ... 19446  2336  9879]
[ 572 7521 6171 ... 6470 2062 9030]
n_epochs=8000, n_batch=32, 1/2=16, b/e=1186, steps=9488000
1/1 [==============================] - 0s 109ms/step
>1, c[0.689,62], d[0.409,1.076], g[0.420]
1/1 [==============================] - 0s 16ms/step
>2, c[0.686,69], d[0.406,1.074], g[0.421]
1/1 [==============================] - 0s 16ms/step
>3, c[0.688,75], d[0.408,1.070], g[0.426]
1/1 [==============================] - 0s 17ms/step
>4, c[0.687,56], d[0.409,1.056], g[0.428]
1/1 [==============================] - 0s 25ms/step
>5, c[0.693,50], d[0.412,1.057], g[0.433]
1/1 [==============================] - 0s 20ms/step
>6, c[0.692,25], d[0.408,1.043], g[0.436]
1/1 [==============================] - 0s 2ms/step
>7, c[0.690,50], d[0.409,1.047], g[0.442]
1/1 [==============================] - 0s 17ms/step
>8, c[0.685,75], d[0.410,1.028], g[0.444]
1/1 [==============================] - 0s 17ms/step
>9, c[0.691,50], d[0.411,1.024], g[0.447]
1/1 [

1/1 [==============================] - 0s 22ms/step
>86, c[0.598,81], d[0.421,0.957], g[0.492]
1/1 [==============================] - 0s 13ms/step
>87, c[0.611,81], d[0.425,0.956], g[0.489]
1/1 [==============================] - 0s 7ms/step
>88, c[0.521,100], d[0.434,0.945], g[0.497]
1/1 [==============================] - 0s 13ms/step
>89, c[0.589,88], d[0.415,0.942], g[0.494]
1/1 [==============================] - 0s 7ms/step
>90, c[0.571,94], d[0.426,0.948], g[0.496]
1/1 [==============================] - 0s 11ms/step
>91, c[0.544,94], d[0.429,0.944], g[0.495]
1/1 [==============================] - 0s 29ms/step
>92, c[0.590,81], d[0.431,0.943], g[0.497]
1/1 [==============================] - 0s 10ms/step
>93, c[0.543,88], d[0.417,0.939], g[0.499]
1/1 [==============================] - 0s 17ms/step
>94, c[0.584,81], d[0.421,0.934], g[0.500]
1/1 [==============================] - 0s 15ms/step
>95, c[0.525,94], d[0.436,0.940], g[0.501]
1/1 [==============================] - 0s 9ms/step


1/1 [==============================] - 0s 25ms/step
>172, c[0.248,94], d[0.351,0.602], g[0.814]
1/1 [==============================] - 0s 21ms/step
>173, c[0.446,88], d[0.440,0.597], g[0.795]
1/1 [==============================] - 0s 23ms/step
>174, c[0.757,69], d[0.427,0.593], g[0.805]
1/1 [==============================] - 0s 26ms/step
>175, c[0.277,94], d[0.462,0.619], g[0.814]
1/1 [==============================] - 0s 30ms/step
>176, c[0.262,88], d[0.337,0.602], g[0.821]
1/1 [==============================] - 0s 22ms/step
>177, c[0.609,69], d[0.373,0.589], g[0.815]
1/1 [==============================] - 0s 24ms/step
>178, c[0.420,81], d[0.423,0.577], g[0.804]
1/1 [==============================] - 0s 27ms/step
>179, c[0.435,81], d[0.428,0.592], g[0.815]
1/1 [==============================] - 0s 32ms/step
>180, c[0.226,94], d[0.400,0.578], g[0.832]
1/1 [==============================] - 0s 16ms/step
>181, c[0.306,94], d[0.406,0.596], g[0.828]
1/1 [==============================] - 0

1/1 [==============================] - 0s 17ms/step
>342, c[0.208,94], d[0.767,0.633], g[0.775]
1/1 [==============================] - 0s 17ms/step
>343, c[0.211,100], d[0.621,0.602], g[0.792]
1/1 [==============================] - 0s 8ms/step
>344, c[0.291,94], d[0.635,0.643], g[0.763]
1/1 [==============================] - 0s 19ms/step
>345, c[0.479,81], d[0.630,0.658], g[0.824]
1/1 [==============================] - 0s 20ms/step
>346, c[0.158,94], d[0.621,0.640], g[0.818]
1/1 [==============================] - 0s 19ms/step
>347, c[0.231,100], d[0.772,0.664], g[0.751]
1/1 [==============================] - 0s 9ms/step
>348, c[0.268,88], d[0.721,0.615], g[0.823]
1/1 [==============================] - 0s 15ms/step
>349, c[0.306,81], d[0.554,0.626], g[0.819]
1/1 [==============================] - 0s 16ms/step
>350, c[0.208,100], d[0.641,0.628], g[0.796]
1/1 [==============================] - 0s 20ms/step
>351, c[0.313,88], d[0.665,0.551], g[0.806]
1/1 [==============================] - 

1/1 [==============================] - 0s 21ms/step
>512, c[0.505,75], d[0.640,0.566], g[0.972]
1/1 [==============================] - 0s 20ms/step
>513, c[0.648,81], d[0.570,0.515], g[0.967]
1/1 [==============================] - 0s 17ms/step
>514, c[0.133,100], d[0.554,0.487], g[0.931]
1/1 [==============================] - 0s 18ms/step
>515, c[0.453,88], d[0.694,0.460], g[0.988]
1/1 [==============================] - 0s 16ms/step
>516, c[0.151,100], d[0.550,0.479], g[0.945]
1/1 [==============================] - 0s 17ms/step
>517, c[0.131,100], d[0.511,0.513], g[0.955]
1/1 [==============================] - 0s 28ms/step
>518, c[0.470,75], d[0.720,0.497], g[0.986]
1/1 [==============================] - 0s 29ms/step
>519, c[0.656,75], d[0.704,0.512], g[0.994]
1/1 [==============================] - 0s 34ms/step
>520, c[0.279,94], d[0.594,0.458], g[0.942]
1/1 [==============================] - 0s 23ms/step
>521, c[0.279,94], d[0.572,0.490], g[0.940]
1/1 [==============================] 

...

1/1 [==============================] - 0s 31ms/step
>59048, c[0.098,94], d[0.515,0.541], g[0.948]
1/1 [==============================] - 0s 31ms/step
>59049, c[0.017,100], d[0.439,0.541], g[0.919]
1/1 [==============================] - 0s 32ms/step
>59050, c[0.008,100], d[0.335,0.596], g[1.144]
1/1 [==============================] - 0s 31ms/step
>59051, c[0.040,100], d[0.501,0.536], g[1.168]
1/1 [==============================] - 0s 32ms/step
>59052, c[0.014,100], d[0.802,0.507], g[0.929]
1/1 [==============================] - 0s 31ms/step
>59053, c[0.032,100], d[0.590,0.425], g[1.151]
1/1 [==============================] - 0s 47ms/step
>59054, c[0.003,100], d[0.564,0.499], g[0.933]
1/1 [==============================] - 0s 31ms/step
>59055, c[0.221,94], d[0.540,0.481], g[0.832]
1/1 [==============================] - 0s 32ms/step
>59056, c[0.059,100], d[0.394,0.469], g[0.891]
1/1 [==============================] - 0s 31ms/step
>59057, c[0.247,88], d[0.821,0.528], g[1.056]
1/1 [========

1/1 [==============================] - 0s 31ms/step
>59131, c[0.236,94], d[0.570,0.565], g[0.963]
1/1 [==============================] - 0s 31ms/step
>59132, c[0.176,88], d[0.670,0.675], g[1.162]
1/1 [==============================] - 0s 31ms/step
>59133, c[0.022,100], d[0.530,0.502], g[0.997]
1/1 [==============================] - 0s 31ms/step
>59134, c[0.146,94], d[0.461,0.477], g[0.987]
1/1 [==============================] - 0s 31ms/step
>59135, c[0.064,100], d[0.541,0.547], g[1.180]
1/1 [==============================] - 0s 31ms/step
>59136, c[0.006,100], d[0.678,0.438], g[1.099]
1/1 [==============================] - 0s 31ms/step
>59137, c[0.105,94], d[0.551,0.532], g[1.078]
1/1 [==============================] - 0s 31ms/step
>59138, c[0.014,100], d[0.459,0.482], g[1.060]
1/1 [==============================] - 0s 31ms/step
>59139, c[0.182,94], d[0.373,0.456], g[1.199]
1/1 [==============================] - 0s 31ms/step
>59140, c[0.120,94], d[0.523,0.472], g[1.097]
1/1 [===========

1/1 [==============================] - 0s 47ms/step
>59214, c[0.009,100], d[0.851,0.387], g[1.168]
1/1 [==============================] - 0s 45ms/step
>59215, c[0.011,100], d[0.443,0.438], g[1.088]
1/1 [==============================] - 0s 31ms/step
>59216, c[0.021,100], d[0.563,0.472], g[1.142]
1/1 [==============================] - 0s 47ms/step
>59217, c[0.088,94], d[0.862,0.381], g[0.978]
1/1 [==============================] - 0s 46ms/step
>59218, c[0.026,100], d[0.534,0.467], g[1.016]
1/1 [==============================] - 0s 44ms/step
>59219, c[0.074,100], d[0.834,0.731], g[1.030]
1/1 [==============================] - 0s 31ms/step
>59220, c[0.060,100], d[0.618,0.585], g[1.048]
1/1 [==============================] - 0s 32ms/step
>59221, c[0.026,100], d[0.624,0.552], g[1.041]
1/1 [==============================] - 0s 31ms/step
>59222, c[0.050,100], d[0.402,0.510], g[0.984]
1/1 [==============================] - 0s 32ms/step
>59223, c[0.035,100], d[0.665,0.498], g[1.112]
1/1 [======

1/1 [==============================] - 0s 31ms/step
>59378, c[0.032,100], d[0.451,0.541], g[1.079]
1/1 [==============================] - 0s 28ms/step
>59379, c[0.006,100], d[0.491,0.499], g[1.045]
1/1 [==============================] - 0s 31ms/step
>59380, c[0.013,100], d[0.400,0.666], g[0.994]
1/1 [==============================] - 0s 29ms/step
>59381, c[0.033,100], d[0.553,0.489], g[1.031]
1/1 [==============================] - 0s 31ms/step
>59382, c[0.039,100], d[0.642,0.604], g[1.062]
1/1 [==============================] - 0s 46ms/step
>59383, c[0.033,100], d[0.538,0.432], g[0.999]
1/1 [==============================] - 0s 47ms/step
>59384, c[0.010,100], d[0.731,0.555], g[0.974]
1/1 [==============================] - 0s 47ms/step
>59385, c[0.026,100], d[0.759,0.568], g[0.924]
1/1 [==============================] - 0s 50ms/step
>59386, c[0.015,100], d[0.652,0.596], g[0.959]
1/1 [==============================] - 0s 31ms/step
>59387, c[0.028,100], d[0.440,0.475], g[0.957]
1/1 [=====

1/1 [==============================] - 0s 32ms/step
>59461, c[0.032,100], d[0.558,0.608], g[1.165]
1/1 [==============================] - 0s 31ms/step
>59462, c[0.048,100], d[0.588,0.468], g[1.174]
1/1 [==============================] - 0s 26ms/step
>59463, c[0.065,94], d[0.551,0.532], g[1.024]
1/1 [==============================] - 0s 46ms/step
>59464, c[0.039,100], d[0.848,0.500], g[1.034]
1/1 [==============================] - 0s 28ms/step
>59465, c[0.013,100], d[0.565,0.594], g[1.190]
1/1 [==============================] - 0s 31ms/step
>59466, c[0.225,94], d[0.558,0.482], g[1.111]
1/1 [==============================] - 0s 44ms/step
>59467, c[0.013,100], d[0.559,0.362], g[1.268]
1/1 [==============================] - 0s 47ms/step
>59468, c[0.092,100], d[0.904,0.421], g[1.140]
1/1 [==============================] - 0s 31ms/step
>59469, c[0.063,100], d[0.722,0.509], g[1.117]
1/1 [==============================] - 0s 36ms/step
>59470, c[0.018,100], d[0.461,0.547], g[1.009]
1/1 [=======

In [1]:
from datetime import datetime

# Lấy ngày giờ hiện tại
hien_tai = datetime.now()

# In ra ngày giờ hiện tại
print("Ngày giờ hiện tại:", hien_tai)

Ngày giờ hiện tại: 2024-07-03 14:34:13.186579
